From ph2_approach_a-Copy5_v2_For_GitHub.ipynb:  Master *

ph2_approach_a_SF_MF_data_ingestion_join.ipynb: √ Data ingestion, prep, feature engineering & selection, joining
ph2_approach_a_SF_MF_EDA.ipynb: (need to make)

ph2_approach_a_SF_model_table.ipynb: 
ph2_approach_a_MF_model_table.ipynb:

ph2_approach_a_SF_visualization_map.ipynb:  
ph2_approach_a_MF_visualization_map.ipynb:  

    
    
    Part 1: Prepare & Join the parcel, shapefiles, fire incident & google ratings data
    Part 2: The Model & Fire Risk Prediction Table
    Part 3: Gathering data for visualization in Tableau
    Part 4: Splitting input csvs to share in GitHub
    References & Links


###  Code Contributors: Margaret Catherman, Yvonne Zhang,  Sanal Shivaprasad & Chiyoung Lee for ATLytiCS & DeKalb County Fire Rescue (DCFR)
    

## Required Input csvs:

    1. Shapefiles: see next chunk
    2. Parcel data: 
        a. 'fire-comm3_owndat.csv' OR 
        b. 'fire-comm3_owndat_00.csv', & fire-comm3_owndat_01.csv'
    3. Fire data: 
        a. 'ATLyticsFiredatacombined.csv', & 'ATLyticsFiredatacombined_2.csv' OR 
        b. 'ATLyticsFiredatacombined_00.csv' to 'ATLyticsFiredatacombined_13.csv' (14 csvs)
    4. Google Ratings API:'Motels Near Dekalb Atlanta version 1.csv', 'Apts Near Dekalb Atlanta version 6.csv'
    
## Generated csvs:

    1. Fire Prediction Table: 'fire_prediction_table_1_client.csv'
    3. Data rejoined with Table for viz, 'all_viz_5R2_v2.csv'
    
## observations:
    
    1. BG_ID_6_tg	487 DCFR area covered



In [1]:
import os
import sys
import pandas as pd
import numpy as np
import requests
import math
import geopandas as gpd
from shapely import wkt
from shapely.geometry import Point
import ast
import re
#from dataprep.clean import clean_address
import seaborn as sns
from datetime import datetime, date
from sklearn import metrics, ensemble, preprocessing
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier
from sklearn.preprocessing import MinMaxScaler, OrdinalEncoder
from sklearn.model_selection import train_test_split,GridSearchCV
from sklearn.metrics import (ConfusionMatrixDisplay, confusion_matrix, brier_score_loss,  f1_score, log_loss,
                             precision_score, recall_score,roc_auc_score, accuracy_score,confusion_matrix, 
                             classification_report,cohen_kappa_score, make_scorer)
from sklearn.feature_selection import mutual_info_classif   
from scipy import stats
from sklearn import calibration
from sklearn.calibration import CalibratedClassifierCV, CalibrationDisplay
from sklearn.linear_model import LogisticRegression
from collections import defaultdict
import folium #for muti-maps
from matplotlib.gridspec import GridSpec
import matplotlib.pyplot as plt
%matplotlib inline
from lazypredict.Supervised import LazyClassifier

import random
import time
import censusgeocode as cg  #MODEL_CONFIG
import censusdata
import csv


pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [2]:
# See https://github.com/atlytics/FireExplorer_Learner/blob/main/models/learner_preprocessor.py 
#for ideas

In [3]:
def unique (df):
    dfun = df.nunique(axis=0)
    dfun_df = pd.DataFrame(dfun) 
    column_names=["Distinct"]
    dfun_df.columns = column_names
    dfun_df_sorted = dfun_df.sort_values('Distinct', ascending=False)
    return (dfun_df_sorted)

def check_missing_values (df):
    percent_missing = df.isnull().sum() * 100 / len(df)
    missing_value_df = pd.DataFrame({'percent_missing': percent_missing})
    missing_value_df.sort_values('percent_missing', inplace=True)
    if missing_value_df['percent_missing'].any():
        return missing_value_df
    else: 
        return "No missing values"


def not_yet_joined (df1, joined_df, variabe_df1):  
    need_to_join= df1[~df1[variabe_df1].isin(joined_df[variabe_df1])]
    #need_to_join.reset_index(drop=True, inplace=True)
    return need_to_join

 
filepath = "/Users/margaretcatherman"
epsg = "4326"  #EPSG correct


# Maps (MF)

In [4]:
#start here

from shapely import wkt
def csv_geo_processor(csv):
    df = pd.read_csv(csv, low_memory=False) #from DF 11/21/22
    df['geometry'] = df['geometry_6'].apply(wkt.loads)
    geodf= gpd.GeoDataFrame(df)
    geodf = geodf.set_crs(epsg=epsg)
    return geodf

pred_mf_stion =  csv_geo_processor('pred_mf_stion.csv')
pred_mf_stion.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 647 entries, 0 to 646
Data columns (total 21 columns):
 #   Column                             Non-Null Count  Dtype   
---  ------                             --------------  -----   
 0   Unnamed: 0                         647 non-null    int64   
 1   BG_ID_6_tg                         647 non-null    int64   
 2   Station_tg                         647 non-null    int64   
 3   Battalion_tg                       647 non-null    int64   
 4   BG_ID_6                            647 non-null    int64   
 5   Predicted_Fire_Probability_6_mf    647 non-null    float64 
 6   Predicted_Fire_Risk_6_mf           647 non-null    object  
 7   Address_mf                         647 non-null    object  
 8   Predicted_Fire_Probability_adr_mf  647 non-null    float64 
 9   Predicted_Fire_Risk_adr_mf         647 non-null    object  
 10  geometry_adr_mf                    647 non-null    object  
 11  Latitude_adr_mf                    64

In [5]:
#  pred_mf_stion.head(2)  #Latitude_adr_mf:  33.81;   Longitude_adr_mf: -84.20

In [6]:
def risk_sequence_processor (pred_mf_stion_a,Predicted_Fire_Probability_6_mf,Predicted_Fire_Risk_6_mf):
    '''
    Code needed to achieve desired sorted order of risk levels.
    '''
    pred_mf_stion_a= pred_mf_stion_a[pred_mf_stion_a.geometry.notnull()]
    pred_mf_stion_a.sort_values([Predicted_Fire_Probability_6_mf],ascending=[False], inplace = True)
    pred_mf_stion_a[Predicted_Fire_Risk_6_mf] = pd.Categorical(pred_mf_stion_a[Predicted_Fire_Risk_6_mf])
    my_order = ["High Risk", "Moderate Risk", "Low Risk"]
    #    pred_mf_stion_a[Predicted_Fire_Risk_6_mf].cat.reorder_categories(my_order, inplace= True)

    pred_mf_stion_a[Predicted_Fire_Risk_6_mf] = pred_mf_stion_a[Predicted_Fire_Risk_6_mf].cat.reorder_categories(my_order)
    pred_mf_stion_a_order = pred_mf_stion_a[pred_mf_stion_a[Predicted_Fire_Risk_6_mf].notna()]
    return pred_mf_stion_a_order


def multi_layer_map_mf():  
    pred_mf_stion_a_geodf = pred_mf_stion.copy()
    pred_mf_stion_a_geodf.drop_duplicates(subset = 'BG_ID_6_tg', inplace = True)
    #pred_mf_stion_a_geodf= gpd.GeoDataFrame(pred_mf_stion_a,geometry= pred_mf_stion_a.geometry_6)  #, geometry=gpd.points_from_xy(fire_3.Longitude_fi, fire_3.Latitude_fi))
    pred_mf_stion_a_order = risk_sequence_processor (pred_mf_stion_a_geodf,'Predicted_Fire_Probability_6_mf', 'Predicted_Fire_Risk_6_mf')
    
    
    pred_mf_stion_b = pred_mf_stion.copy()  ##geometry_adr_mf
    pred_mf_stion_b.drop_duplicates(subset = 'Address_mf', inplace = True)
    pred_mf_stion_b.drop(['geometry'], axis = 1, inplace=True)
    pred_mf_stion_b['geometry'] = pred_mf_stion_b['geometry_adr_mf'].apply(wkt.loads)
    pred_mf_stion_b['centerpoint'] = pred_mf_stion_b['geometry'].centroid
    pred_mf_stion_b.drop('geometry',axis=1, inplace=True)
    pred_mf_stion_b= pred_mf_stion_b.rename(columns={'centerpoint': 'geometry'})
    pred_mf_stion_b_order = risk_sequence_processor (pred_mf_stion_b,'Predicted_Fire_Probability_adr_mf', 'Predicted_Fire_Risk_adr_mf')


    mm = pred_mf_stion_a_order.explore(
                column="Predicted_Fire_Risk_6_mf",  # make choropleth based on "POP2010" column
                scheme="naturalbreaks",  # use mapclassify's natural breaks scheme
                legend=True, #loc='lower left', # show legend
                cmap= 'autumn',
                legend_kwds={"loc": 'center right'},
                k=10,  # use 10 bin
                tooltip = False, # do not
                popup=["BG_ID_6_tg", "Station_tg", "Battalion_tg"],  # show popup (on-click)
                name="stations",  # name of the layer in the map
            )

    pred_mf_stion_b_order.explore(
            m=mm,  # pass the map object
            column="Predicted_Fire_Risk_adr_mf",  # make choropleth based on "BoroName" column
            scheme="naturalbreaks",  # use mapclassify's natural breaks scheme
            legend=False,  # show legend
            cmap ='gist_gray',
            tooltip=["Predicted_Fire_Risk_adr_mf","Address_mf","Latitude_adr_mf", "Longitude_adr_mf"],                    
            tooltip_kwds=dict(labels=False),  #legend_kwds=dict(colorbar=False),  # 
            name=" BG_ID_9",  # name of the layer in the map
        )

    folium.LayerControl().add_to(mm)  # use folium to add layer control
    return mm
mf_map=multi_layer_map_mf()
mf_map
#mf: Predicted_Fire_Risk_6_mf, BG_ID_6_tg autumn-shaded; & Predicted_Fire_Risk_adr_mf, gist_gray-dots
#sf: Predicted_Fire_Risk_6_sf, BG_ID_6 autumn-shaded;    & Predicted_Fire_Risk_9_sf, gist_gray-dots


# MF, above. 647 properties witin DCFR area.

        1. By Address:        
        High Risk        377 black dots 
        Moderate Risk     64 gray dots
        Low Risk         206 white dots
        
        2. By BG_ID_6:
        High Risk        169
        Moderate Risk     31
        Low Risk          25
